# Optimization for a Mixed-Assets Portfolio

## I. Loading Libraries

In [1]:
import yfinance as yf
import pandas as pd
import numpy as np
import plotly.express as px
import bls

from pypfopt.efficient_frontier import EfficientFrontier
from pypfopt.discrete_allocation import DiscreteAllocation

In [ ]:
# DATA INPUT 
## Tickers
assets = []
s = int(input("Number of stocks in the portfolio is: "))
for i in range(s):
    x = str(input("Stock ticker # %d: " %(i+1))).upper()
    assets.append(x)
c = int(input("Number of cryptocurrency in the portfolio is: "))
for i in range(c):
    x = str(input("Cryptocurrency ticker # %d: " %(i+1))).upper()
    assets.append(x)
print("List of assets: ", assets)
print("Number of assets: ", s+c)

##Time Period 
start_date = input("Data collected starting date (yyyy-mm-dd): ")
end_date = input("Data collected ending date (yyyy-mm-dd): ")

#### b. Downloading data

In [ ]:
## Main-dataframes
assets_data = yf.download(assets, 
                          start = start_date, 
                          end = end_date)
## Sub-dataframes
adj_assets_data = assets_data.loc[:,"Adj Close"]
volume_assets_data = assets_data.loc[:,"Volume"]
cumlt_return_data = adj_assets_data.dropna().div(adj_assets_data.dropna().iloc[0]/100)
daily_returns = adj_assets_data.pct_change()
monthly_returns = adj_assets_data.dropna().resample('M').ffill().pct_change()

### 2. Inflation (Consumer Price Index) Data 

#### a. Downloading Data

In [70]:
## Main-dataframes
cpi_data = bls.get_series('CUUR0000SA0', startyear=int(str(start_date)[:4]), endyear=int(str(end_date)[:4])).to_frame()
## Sub-dataframes
cpi_monthly_returns = cpi_data.dropna().resample('M').ffill().pct_change()
cpi_returns_list = cpi_monthly_returns.CUUR0000SA0.values.tolist()
combined_monthly_returns = monthly_returns.head(len(cpi_returns_list)).assign(CPI = cpi_returns_list)

## III. Financial Analyses

### 1. Statistical Data

#### a. Return

In [71]:
## Daily Returns Mean
daily_return_mean = daily_returns.mean()
## Annualized Expected Returns
annual_expected_return = daily_return_mean*252

#### b. Risk

In [72]:
## Daily returns standard deviation
std = daily_returns.std()
## Annualized Standard Deviation
annual_std = std*(np.sqrt(252))

#### c. Covariance and Correlation

In [73]:
## Covariance 
covariance_assets = daily_returns.cov()
## Annualized Covariance 
annual_covariance = covariance_assets*252

## Correlation
correlation_assets = daily_returns.corr()

### 2. Historical Price and Volume

#### a. Price Chart

In [49]:
# PRICE CHART
## Linear
price_ln_fig = px.line(adj_assets_data, color_discrete_sequence=px.colors.sequential.Electric)
price_ln_fig.update_layout(
    title={
        'text': "Price Chart <br> (Linear Scale)",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, 
    xaxis_title="Year",
    yaxis_title="Price <br> (in U.S. Dollar)",
    legend_title="Asset"
)
price_ln_fig.show()

## Logarithmic
price_log_fig = px.line(adj_assets_data, color_discrete_sequence=px.colors.sequential.Electric)
price_log_fig.update_layout(
    title={
        'text': "Price Chart <br> (Logarithmic Scale)",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, 
    xaxis_title="Year",
    yaxis_title="Price <br> (in U.S Dollar)",
    legend_title="Asset"
)
price_log_fig.update_yaxes(type="log")
price_log_fig.show()

#### b. Volume Chart

In [50]:
# VOLUME CHART
## Linear
volume_ln_fig = px.line(volume_assets_data, color_discrete_sequence=px.colors.sequential.Electric)
volume_ln_fig.update_layout(
    title={
        'text': "Volume Chart <br> (Linear Scale)",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, 
    xaxis_title="Year",
    yaxis_title="Volume",
    legend_title="Asset"
)
volume_ln_fig.show()

## Logarithmic
volume_log_fig = px.line(volume_assets_data, color_discrete_sequence=px.colors.sequential.Electric)
volume_log_fig.update_layout(
    title={
        'text': "Volume Chart <br> (Logarithmic Scale)",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, 
    xaxis_title="Year",
    yaxis_title="Volume",
    legend_title="Asset"
)
volume_log_fig.update_yaxes(type="log")
volume_log_fig.show()

### 3. Cumulative Return

#### a. Cumulative Return Chart

In [51]:
# CUMULATIVE RETURN
## Graph
cumlt_return_fig = px.line(cumlt_return_data, color_discrete_sequence=px.colors.sequential.Electric)
cumlt_return_fig.update_layout(
    title={
        'text': "Cumulative Return",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, 
    xaxis_title="Year",
    yaxis_title="Value <br> (in U.S. Dollar)",
    legend_title="Asset"
)
cumlt_return_fig.update_yaxes(type="log")
cumlt_return_fig.show()

#### b. Total Value on December 30, 2022

In [ ]:
cumlt_return_data.tail(1)

### 4. Assets' Correlation to Inflation

#### a. Correlation Table

In [ ]:
### Calculating
correlation_cpi = (combined_monthly_returns.corr()['CPI'].to_frame()).T
correlation_cpi

#### b. Correlation Heatmap

In [ ]:
### Correlation heatmap between assets and CPI
cor_fig_cpi = px.imshow(correlation_cpi, text_auto=True, color_continuous_scale = "Electric")
cor_fig_cpi.update_layout(
    title={
        'text': "Correlation between each Asset and CPI",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}
)
cor_fig_cpi.show()

### 5. Assets' Risks

#### a. Assets' Risk based on Daily Returns

In [55]:
risk_fig = px.box(daily_returns, color_discrete_sequence=px.colors.sequential.Electric)
risk_fig.update_layout(
    title={
        'text': "Assets Risk based on Daily Returns",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, 
    xaxis_title="Asset",
    yaxis_title="Daily Return"
)
risk_fig.show()

#### b. Assets' Risk based on Sharpe Ratio

In [ ]:
## Sharpe Ratio
sharpe_ratio_assets = (((annual_expected_return/annual_std).to_frame())).T
sharpe_ratio_assets.index = ["Sharpe Ratio"]
### Assets Sharpe Ratios
sharpe_fig_assets = px.imshow(sharpe_ratio_assets, text_auto=True, color_continuous_scale = "Electric")
sharpe_fig_assets.update_xaxes(side="top")
sharpe_fig_assets.update_layout(
    title={
        'text': "Assets' Sharpe Ratio",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}
)
sharpe_fig_assets.show()

sharpe_ratio_assets

### 6. Assets Correlation

#### a. Correlation Table

In [ ]:
correlation_assets

#### b. Correlation Heatmap

In [58]:
### Correlation heatmap among assets
cor_fig_assets = px.imshow(correlation_assets, text_auto=True, color_continuous_scale = "Electric")
cor_fig_assets.update_layout(
    title={
        'text': "Correlation heatmap among assets",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}
)
cor_fig_assets.show()

## IV. Portfolio Optimization

### 1. Risk-free Rate

#### a. Input Risk-free rate

In [ ]:
risk_free = float(input("Annual Risk-free Rate is: "))

### 2. Portfolio Optimization

#### a. Monte Carlo Simulation

In [ ]:
num_ports = int(input("Number of trials in the simulation is: "))

## Zero Arrays Setup
all_weights = np.zeros((num_ports, (int(s+c))))
return_arr = np.zeros(num_ports)
risk_arr = np.zeros(num_ports)
sharpe_arr = np.zeros(num_ports)

## Monte Carlo Simulation
for n in range(num_ports):
    #Weights:
    weights = np.array(np.random.random(int(s+c)))
    weights = weights/np.sum(weights)
    all_weights[n,:] = weights
    
    #Expected Return
    return_arr[n] = np.sum(annual_expected_return*weights)
    
    # Expected Risk
    risk_arr[n] = np.sqrt(np.dot(weights.T, np.dot(annual_covariance, weights)))
    
    # Sharpe Ratio
    sharpe_arr[n] = (return_arr[n] - risk_free)/risk_arr[n]

#### b. Efficient Frontier

In [61]:
eff_frt = px.scatter(x = risk_arr, y = return_arr, color = sharpe_arr, color_continuous_scale = "Electric")
eff_frt.update_layout(
    title={
        'text': "Efficient Frontier",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, 
    xaxis_title="Risk <br> (Standard Deviation)",
    yaxis_title="Expected Return",
    coloraxis_colorbar=dict(title="Sharpe Ratio")
)
eff_frt.show()

#### c. Optimal Portfolio

##### * Optimal Portfolio Weights

In [ ]:
ef = EfficientFrontier(annual_expected_return,annual_covariance)
weights = ef.max_sharpe() 
cleaned_weights = ef.clean_weights()
assets_list = list(cleaned_weights.keys())
values = list(cleaned_weights.values())

allocation_fig = px.pie (values = values, names = assets_list, color_discrete_sequence=px.colors.sequential.Electric)
allocation_fig.update_layout(
    title={
        'text': "Optimal Portfolio Allocation <br> (Without Bitcoin)",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}
)
allocation_fig.show()

##### * Optimal Portfolio Statistics

In [ ]:
ef.portfolio_performance(verbose=True)

In [ ]:
cleaned_weights